In [30]:
import chess
import chess.pgn

In [2]:
import chess_transformer
import torch

import pickle

%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [44]:
model = chess_transformer.ChessNet()
state_dict = torch.load("models/chess-transform.pth")
model.load_state_dict(state_dict)

with open("data/move_encoder.pkl", "rb") as f:
    encoder = pickle.load(f)

a = encoder.transform(['e3'])

x_init = torch.tensor([a])
x_game = x_init
print(x_game.shape)
with torch.no_grad():
    for _ in range(50):
        next_move = torch.argmax(model(x_game),dim=1).unsqueeze(0)
        x_game = torch.cat((x_game, next_move), dim=1)

print(x_game)
game = x_game.squeeze(1).detach().numpy()

for move in game:
    print(encoder.inverse_transform(move))

torch.Size([1, 1])
tensor([[36237,  4653,  8775,  8775, 12066,  8703,  8703,  8703,  8703,  8703,
          8703,  8703,  8703,  8703,  8703,  8703,  8703,  8703,  8703,  8703,
          8703,  8703,  8703,  8703,  8703,  8703,  8703,  8703,  8703,  8703,
          8703,  8703,  8703,  8703,  8703,  8703,  8703,  8703,  8703,  8703,
          8703,  8703,  8703,  8703,  8703,  8703,  8703,  8703,  8703,  8703,
          8703]])
['e3' 'Bd2' 'Kf6' 'Kf6' 'Ne3' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6'
 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6'
 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6'
 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6' 'Kc6'
 'Kc6' 'Kc6' 'Kc6']


In [41]:
with open("data/lichess_elite_2024-06.pgn") as pgn:
    for _ in range(2):
        game = chess.pgn.read_game(pgn)
parsed_game = datasets.parse_pgn(game, encoder)
print(parsed_game)
print(len(parsed_game))


l = datasets.generate_games_list()
print(len(l))

[35964 36246 36513 36105  7137 12747 12594  5850 13920 13920 36102 12117
 20031 36381 35823 35970  2538  8454 13734 11742 18543 36519 32334 36516
 12000 36657 11538 36654 36375 13878 36696 36696 34398 27969 21567 36558
 36330 29081  8760 27969 36060 36288 24981 29127 13857 35739 10971 35736
 35826 10713 12066 35733 33084 32271 32676 11742 13221 33507 12272  8781
 13797 35595 13860 12168 13878 11061 36378 33915  8763 35832 35829 36012
 35610 35826 33504 10362  4860 33912 33509 33915 33504 33912 35640  8946
 12698  8775 12066 13758  8478 32283  8766 35829 13145  8802 36381 33099
  8769 33084 36386  8781  5781 35823 12168 33089  8742 33096  8478 33086
  8721 35556  8724 32673  8751 33897  8727 35634  8940 35826  8721 35823
  8694 35865  8670 35724  8649 29133  8838 23751]
128
100


In [42]:
print(l[0])

[36240 36243 12594 11163 36102 36285 13809 12747 11010  3231 13791 35925
  4710 13920 13920 36105 36288 36060  7308 35970 24828 32691  8583 29133
 29133 36567 12027  4941 35823 35967 32358  5781 13104 34419 34422 35964
  5493 36381  6390  3231 33897 36102 35919  8505 33906 36378 34724  8781
 13542  8451 12747 36660 34719  5781 35655  5850 13143 32673  5619  7308
 34314  8580  8580 35739 32262 33498  4710 32679 36513 35736 36654  4653
 12747 32274 11744  8754 12168 35634 36378 32274 33486  5552  8787 35733
 32262 35730 35961 36144  3849 32673  8766 35577  8934 32673  8745 32670
 35529 35529 36381 33078 36386  8967  8769  8802 36516 33897 36519 33909
 36617 35709  8793 34727  8820 33909  8793 34302  8790 35958 36657 35952
 36662  8826  8787 34727  8811 35119]


In [10]:
pe = torch.zeros(1000, k)
pe[:, 0::2]

tensor([[0., 0.],
        [0., 0.],
        [0., 0.],
        ...,
        [0., 0.],
        [0., 0.],
        [0., 0.]])

In [14]:
dmodel = 10 
b, k, t = 2, 6, 5
x = torch.rand([b, t, k])
net = chess_transformer.PositionalEncoding(k)

print(x)
print(net(x))


tensor([[[0.8877, 0.7697, 0.8870, 0.3310, 0.5819, 0.7942],
         [0.6578, 0.8942, 0.6031, 0.9392, 0.4993, 0.7025],
         [0.1388, 0.5313, 0.6307, 0.2958, 0.7141, 0.7189],
         [0.7735, 0.0328, 0.4540, 0.5745, 0.0201, 0.9242],
         [0.3022, 0.4990, 0.8973, 0.8409, 0.6073, 0.0774]],

        [[0.2941, 0.0978, 0.0776, 0.2264, 0.5547, 0.8798],
         [0.6163, 0.9308, 0.0569, 0.5647, 0.1226, 0.9038],
         [0.6873, 0.3491, 0.3050, 0.4508, 0.3950, 0.8107],
         [0.6549, 0.6126, 0.1424, 0.0599, 0.2733, 0.2347],
         [0.6569, 0.4541, 0.7090, 0.0558, 0.4156, 0.1356]]])
tensor([[[ 0.8877,  1.7697,  0.8870,  1.3310,  0.5819,  1.7942],
         [ 1.4992,  1.4345,  0.6495,  1.9381,  0.5015,  1.7025],
         [ 1.0481,  0.1151,  0.7234,  1.2915,  0.7184,  1.7189],
         [ 0.9146, -0.9572,  0.5928,  1.5649,  0.0265,  1.9242],
         [-0.4546, -0.1547,  1.0819,  1.8237,  0.6160,  1.0774]],

        [[ 0.2941,  1.0978,  0.0776,  1.2264,  0.5547,  1.8798],
         [ 1.4

In [120]:

with open("data/lichess_elite_2024-06.pgn") as pgn:
    first_game = chess.pgn.read_game(pgn)
    i = 0
    for _ in pgn:
        i += 1
print(i)

game_lengths = []
all_games = []
    
with open("data/lichess_elite_2024-06.pgn") as pgn:
    for _ in range(10000):
        game = chess.pgn.read_game(pgn)
        pgame = parse_pgn(game)
        all_games.append(pgame)
        game_lengths.append(len(pgame))

with open("data/lichess_elite_2021-11.pgn") as pgn:
    for _ in range(10000):
        game = chess.pgn.read_game(pgn)
        pgame = parse_pgn(game)
        all_games.append(pgame)
        game_lengths.append(len(pgame))


        
 
print(max(game_lengths))


print(first_game.mainline())

first_game.headers["Result"]

6849462
593
1. e4 e5 2. Nf3 Nc6 3. d4 exd4 4. Nxd4 Nf6 5. Nc3 Bb4 6. Nxc6 bxc6 7. Bd3 O-O 8. O-O d5 9. exd5 cxd5 10. Bg5 c6 11. Qf3 Rb8 12. Bxf6 Qxf6 13. Qxf6 gxf6 14. Ne2 Bd6 15. b3 c5 16. Rad1 Be6 17. Ng3 Rfd8 18. Rfe1 c4 19. Be2 f5 20. Bf3 Bb4 21. Re2 d4 22. bxc4 Bxc4 23. Re5 f4 24. Rg5+ Kf8 25. Nh5 Bxa2 26. Nf6 h6 27. Rg4 Be6 28. Rxf4 Be7 29. Ng4 Rb2 30. Be4 Bg5 31. Rf5 Bxf5 32. Bxf5 a5 33. Ra1 Rd5 34. Bd3 Rb4 35. g3 a4 36. h4 Bd2 37. Nf6 Ra5 38. Nd7+ Ke7 39. Ne5 Rxe5 40. f4 Ra5 41. Rd1 Be3+ 42. Kg2 a3 43. Ra1 a2 44. c3 dxc3 45. Bc2 Rb2 46. Kf3 Rxc2 47. Kxe3 Rb2 48. Ke4 Rb1 49. Rxa2 Rxa2 50. f5 Rc1 51. f6+ Kxf6 52. Kf4 Kg7 53. g4 Re2 54. g5 Re6 55. gxh6+ Rxh6 56. Kg4 Rg6+ 57. Kh5 Re6 58. Kg4 Rf1 59. Kg3 c2 60. h5 c1=Q 61. h6+ Kh7 62. Kg2 Rg6+ 63. Kh2 Rh1#


'0-1'

In [129]:
distinct_moves = {'e4' : 0}
with open("data/lichess_elite_2024-06.pgn") as pgn:
    for _ in range(20000):
        for move in parse_pgn(chess.pgn.read_game(pgn)):
            if move in distinct_moves:
                distinct_moves[move] += 1
            else: 
                distinct_moves[move] = 1

print(len(distinct_moves))
# print(distinct_moves)


4533


In [30]:
def parse_pgn(game):
    board = game.board()
    moves = []
    for move in game.mainline_moves():
        moves.append(board.san(move))
        board.push(move)
    return moves

parsed_first_game  = parse_pgn(first_game)
print(parsed_first_game)
print(len(parsed_first_game))

['e4', 'e5', 'Nf3', 'Nc6', 'd4', 'exd4', 'Nxd4', 'Nf6', 'Nc3', 'Bb4', 'Nxc6', 'bxc6', 'Bd3', 'O-O', 'O-O', 'd5', 'exd5', 'cxd5', 'Bg5', 'c6', 'Qf3', 'Rb8', 'Bxf6', 'Qxf6', 'Qxf6', 'gxf6', 'Ne2', 'Bd6', 'b3', 'c5', 'Rad1', 'Be6', 'Ng3', 'Rfd8', 'Rfe1', 'c4', 'Be2', 'f5', 'Bf3', 'Bb4', 'Re2', 'd4', 'bxc4', 'Bxc4', 'Re5', 'f4', 'Rg5+', 'Kf8', 'Nh5', 'Bxa2', 'Nf6', 'h6', 'Rg4', 'Be6', 'Rxf4', 'Be7', 'Ng4', 'Rb2', 'Be4', 'Bg5', 'Rf5', 'Bxf5', 'Bxf5', 'a5', 'Ra1', 'Rd5', 'Bd3', 'Rb4', 'g3', 'a4', 'h4', 'Bd2', 'Nf6', 'Ra5', 'Nd7+', 'Ke7', 'Ne5', 'Rxe5', 'f4', 'Ra5', 'Rd1', 'Be3+', 'Kg2', 'a3', 'Ra1', 'a2', 'c3', 'dxc3', 'Bc2', 'Rb2', 'Kf3', 'Rxc2', 'Kxe3', 'Rb2', 'Ke4', 'Rb1', 'Rxa2', 'Rxa2', 'f5', 'Rc1', 'f6+', 'Kxf6', 'Kf4', 'Kg7', 'g4', 'Re2', 'g5', 'Re6', 'gxh6+', 'Rxh6', 'Kg4', 'Rg6+', 'Kh5', 'Re6', 'Kg4', 'Rf1', 'Kg3', 'c2', 'h5', 'c1=Q', 'h6+', 'Kh7', 'Kg2', 'Rg6+', 'Kh2', 'Rh1#']
126
128


In [19]:
def can_move(piece_type, start, end):
    board = chess.Board(None)
    start_square = chess.parse_square(start)
    end_square = chess.parse_square(end)
    piece = chess.Piece.from_symbol(piece_type)
    board.set_piece_at(start_square, piece)
    
    return chess.Move(start_square, end_square) in list(board.legal_moves)

print(can_move('B', 'f1', 'e2'))

True


In [25]:
def generate_all_pawn_moves():
    files = ['a', 'b', 'c', 'd', 'e', 'f', 'g', 'h']
    white_pawn_moves = []
    black_pawn_moves = []

    # White Pawn Moves: Forward Moves and Promotions
    for file in files:
        for rank in ['2', '3', '4', '5', '6']:
            white_pawn_moves.append(file + str(int(rank) + 1))  # Single move
        white_pawn_moves.append(file + '4')  # Double move from rank 2

    # Black Pawn Moves: Forward Moves and Promotions
    for file in files:
        for rank in ['7', '6', '5', '4', '3']:
            black_pawn_moves.append(file + str(int(rank) - 1))  # Single move
        black_pawn_moves.append(file + '5')  # Double move from rank 7

    # Promotions for White Pawns
    promotions = ['Q', 'R', 'B', 'N']
    for file in files:
        for promotion in promotions:
            white_pawn_moves.append(file + '8=' + promotion)

    # Promotions for Black Pawns
    for file in files:
        for promotion in promotions:
            black_pawn_moves.append(file + '1=' + promotion)

    # Captures for White Pawns
    for file in files:
        for rank in ['2', '3', '4', '5', '6', '7']:
            if file != 'a':
                white_pawn_moves.append(file + 'x' + chr(ord(file) - 1) + str(int(rank) + 1))  # Capture left
            if file != 'h':
                white_pawn_moves.append(file + 'x' + chr(ord(file) + 1) + str(int(rank) + 1))  # Capture right

    # Captures for Black Pawns
    for file in files:
        for rank in ['7', '6', '5', '4', '3', '2']:
            if file != 'a':
                black_pawn_moves.append(file + 'x' + chr(ord(file) - 1) + str(int(rank) - 1))  # Capture left
            if file != 'h':
                black_pawn_moves.append(file + 'x' + chr(ord(file) + 1) + str(int(rank) - 1))  # Capture right

    # Capture promotions for White Pawns
    for file in files:
        if file != 'a':
            for promotion in promotions:
                white_pawn_moves.append(file + 'x' + chr(ord(file) - 1) + '8=' + promotion)
                # white_pawn_moves.append(file + 'x' + chr(ord(file) - 1) + '8' + promotion.lower())
        if file != 'h':
            for promotion in promotions:
                white_pawn_moves.append(file + 'x' + chr(ord(file) + 1) + '8=' + promotion)
                # white_pawn_moves.append(file + 'x' + chr(ord(file) + 1) + '8' + promotion.lower())

    # Capture promotions for Black Pawns
    for file in files:
        if file != 'a':
            for promotion in promotions:
                black_pawn_moves.append(file + 'x' + chr(ord(file) - 1) + '1=' + promotion)
                # black_pawn_moves.append(file + 'x' + chr(ord(file) - 1) + '1' + promotion.lower())
        if file != 'h':
            for promotion in promotions:
                black_pawn_moves.append(file + 'x' + chr(ord(file) + 1) + '1=' + promotion)
                # black_pawn_moves.append(file + 'x' + chr(ord(file) + 1) + '1' + promotion.lower())

    return white_pawn_moves + black_pawn_moves


def generate_all_piece_moves():
    files = ['a', 'b', 'c', 'd', 'e', 'f', 'g', 'h']
    ranks = ['1', '2', '3', '4', '5', '6', '7', '8']
    pieces = ['N', 'B', 'R', 'Q', 'K']
    piece_moves = []

    # Generate all possible moves for each piece type
    for piece in pieces:
        for start_file in files:
            for start_rank in ranks:
                for end_file in files:
                    for end_rank in ranks:
                        if not(can_move(piece, start_file+start_rank, end_file+end_rank)):
                            continue

                        # Basic move
                        piece_moves.append(piece + end_file + end_rank)

                        # Capture
                        piece_moves.append(piece + 'x' + end_file + end_rank)

                        if not(piece in ['K']):
                            # File disambiguation
                            piece_moves.append(piece + start_file + end_file + end_rank)  
                            piece_moves.append(piece + start_file + 'x' + end_file + end_rank)
                            # Rank disambiguation
                            piece_moves.append(piece + start_rank + end_file + end_rank)
                            piece_moves.append(piece + start_rank + 'x' + end_file + end_rank)

                        # Full disambiguation
                        if piece in ['N', 'B', 'Q']:
                            piece_moves.append(piece + start_file + start_rank + end_file + end_rank)
                            piece_moves.append(piece + start_file + start_rank + 'x' + end_file + end_rank)

    return piece_moves


def generate_castling_moves():
    return ['O-O', 'O-O-O']


def add_checks_and_checkmates(moves):
    checked_moves = []
    for move in moves:
        checked_moves.append(move + '+')  # Check
        checked_moves.append(move + '#')  # Checkmate
    return moves + checked_moves


# Generate all possible moves
pawn_moves = generate_all_pawn_moves()
piece_moves = generate_all_piece_moves()
castling_moves = generate_castling_moves()

# Combine and add checks/checkmates
all_moves = pawn_moves + piece_moves + castling_moves
all_moves = add_checks_and_checkmates(all_moves)

# Remove duplicates
all_moves = list(set(all_moves))
print(len(all_moves))

# Print the moves


36726


In [22]:
print('Bf1g2#' in all_moves)
print( can_move('B', 'f1', 'g2'))


True
True


In [30]:
from sklearn.preprocessing import LabelEncoder

# Sample chess moves

# Initialize the label encoder
move_encoder = LabelEncoder()

# Fit the encoder to the list of moves
move_encoder.fit(all_moves)

# Transform the moves into encoded values
encoded_moves = move_encoder.transform(['Be1'])


# print("Original Moves:", all_moves)
# print("Encoded Moves:", encoded_moves)


[5448]


In [21]:
print(len(encoded_moves))

36726


In [25]:
import datasets
import pickle

In [22]:
games_list= datasets.generate_games_list()

0.0010118484497070312


In [26]:
with open("data/move_encoder.pkl", "rb") as f:
        encoder = pickle.load(f)
        

In [49]:
print(len(encoder.classes_))
print(encoder.inverse_transform([-1]))

36726


ValueError: y contains previously unseen labels: [-1]

In [53]:
from torch import nn
k = 10 
embedder = nn.Embedding(36726, k, padding_idx=-1)

a = torch.tensor([-1])
embedder(a)



IndexError: index out of range in self

In [44]:

from torch.utils.data import DataLoader

games_list = datasets.generate_games_list()
dataset = datasets.NextMoveDataset(games_list)
dataloader = DataLoader(
    dataset, batch_size=2, shuffle=True, collate_fn=lambda batch: tuple(zip(*batch))
)

In [45]:
for x in dataloader: 
    print(x)

((tensor([36240, 36246, 36102, 36105, 11499, 35742, 36513, 35967,  7137]), tensor([36240, 35967, 11010, 11163, 36378, 36108, 12594, 36246,  3288,  5010,
        13920, 35742,  8511,  8511, 36381, 12747, 36429, 36429, 13182, 22344,
        35661, 36567, 28100])), (tensor(36057), tensor(8754)))
((tensor([12594, 36105, 36240, 36195, 13182, 36243, 36099, 36282,  8526, 11163,
        13920,  5850, 12594,  4941, 11010, 36660, 35733, 12747, 35826, 13920,
         3117,  7251, 36651,  8004, 33894, 11589, 36516, 13881, 36699,  8601,
         5493,  6528,  4710,  7251,  5493, 13829, 29097, 25287,  8787, 35739,
        23268,  5781, 13836, 34443,  8784, 25134, 23421, 26648, 26223, 29147,
         8979,  8556, 35634,  7916,  9006, 35634, 33486, 34035, 33495, 32379,
        33087, 35781, 35781, 33894,  8787, 35970, 35829, 33909, 35832, 35967,
        10335, 33498, 34719, 36519, 34716, 34314, 33084, 33897, 13788, 34643,
         8784, 34715,  8760, 35577, 35577, 35577,  4779, 33087,  5550, 35586,
  